In [1]:
!pip install captum
!pip install transformers
!pip install shap
!pip install zhon
from captum.attr import visualization as viz
from captum.attr import LayerConductance, LayerIntegratedGradients
from transformers import BertForSequenceClassification, AdamW, BertConfig, BertTokenizer

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.4 MB 5.1 MB/s 
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4.4 MB 5.1 MB/s 
     |████████████████████████████████| 101 kB 8.3 MB/s 
     |████████████████████████████████| 6.6 MB 32.6 MB/s 
     |████████████████████████████████| 596 kB 48.0 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 569 kB 3.3 MB/s 
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 99 kB 4.1 MB/s 
  Created wheel for zhon: filename=zhon-1.1.5-py3-none-

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
######test##############
import numpy as np
import pandas as pd
import time
import re

In [4]:
import transformers
import shap
import jieba
import re
from zhon.hanzi import punctuation
import torch

In [5]:
from ast import literal_eval

## 定义模型

In [6]:
device = torch.device("cpu")

In [7]:
# 加载 BertForSequenceClassification, 预训练 BERT 模型 + 顶层的线性分类层 
model = BertForSequenceClassification.from_pretrained(
#     "model/bert-base-chinese-FineTuned-Binary-Best", # 小写的 12 层预训练模型
    "/content/drive/MyDrive/train（result_6）", # 小写的 12 层预训练模型
    num_labels = 2, # 分类数 --2 表示二分类
                    # 你可以改变这个数字，用于多分类任务  
#     output_attentions = False, # 模型是否返回 attentions weights.
#     output_hidden_states = False, # 模型是否返回所有隐层状态.
)
model.to(device)
model.eval()
model.zero_grad()

In [8]:
tokenizer = BertTokenizer.from_pretrained('/content/drive/MyDrive/train（result_6）')

## 导入数据

In [44]:
df = pd.read_csv("/content/drive/MyDrive/情感打分数据包/中文/7月26日demo_new.csv")
df

Unnamed: 0                                                txt        year  \
0           0  坚持罢工争取增资【新华社陕北十八日电】东京消息：日本海员工人继续大罢工。全日海员工会，在与政...  1948.12.20   
1           1  和平集会在纪念馆和平广场举行。侵华日军南京大屠杀遇难同胞纪念馆馆长朱成山表示，在这个具有纪念...  2012.08.16   

   text_length                                            txt_seg  Topic  \
0          470  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...    299   
1          686  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...    228   

   Doc_ID                                              Score  label  \
0   80956  [-0.17992433482732492, -0.1460053249588042, -0...      6   
1   38843  [0.015359698043600992, 0.03786564722019095, 0....      6   

             negative_score           positicve_score  positicve_score__mean  \
0   [0.7293623, 0.08481447]   [0.27063772, 0.9151855]               0.592912   
1  [0.49792624, 0.81404465]  [0.50207376, 0.18595535]               0.344015   

   negative_score_mean                                               text  \
0             0.407088  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...   
1             0.655985  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...   

                                              nopunc  
0  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...  
1  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...

### 先分词

In [45]:
df['Phrase']=df.nopunc.apply(lambda x: x.split(' '))
df

Unnamed: 0                                                txt        year  \
0           0  坚持罢工争取增资【新华社陕北十八日电】东京消息：日本海员工人继续大罢工。全日海员工会，在与政...  1948.12.20   
1           1  和平集会在纪念馆和平广场举行。侵华日军南京大屠杀遇难同胞纪念馆馆长朱成山表示，在这个具有纪念...  2012.08.16   

   text_length                                            txt_seg  Topic  \
0          470  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...    299   
1          686  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...    228   

   Doc_ID                                              Score  label  \
0   80956  [-0.17992433482732492, -0.1460053249588042, -0...      6   
1   38843  [0.015359698043600992, 0.03786564722019095, 0....      6   

             negative_score           positicve_score  positicve_score__mean  \
0   [0.7293623, 0.08481447]   [0.27063772, 0.9151855]               0.592912   
1  [0.49792624, 0.81404465]  [0.50207376, 0.18595535]               0.344015   

   negative_score_mean                                               text  \
0             0.407088  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...   
1             0.655985  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...   

                                              nopunc  \
0  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...   
1  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...   

                                              Phrase  
0  [坚持, 罢工, 争取, 增资, 新华社, 陕北, 十八日, 电, 东京, 消息, 日本海,...  
1  [和平, 集会, 在, 纪念馆, 和平, 广场, 举行, 侵华日军南京大屠杀遇难同胞纪念馆,...

### getlabel 和 pred_pro

In [46]:
import torch.nn.functional as F
def split_chunk(text): #为什么要split_chunk, 512的数值有意义吗
    str = text
#     str = re.sub(r"\s+", "", str)
    str = str.strip()
    n = 512
    chunks = []
    i = 0
    while i < len(str):
        if i+n < len(str):
            chunks.append(str[i:i+n])
        else:
            chunks.append(str[i:len(str)])
        i += n
    return(chunks)


def getlb(txt):
    chunk_sample=split_chunk(txt)
    res = []
    for i in range(len(chunk_sample)):
        inp = tokenizer(chunk_sample[i], return_tensors='pt', padding="max_length", max_length=512)
        output = model(**inp)
        # output
        # output = F.softmax(output.pooler_output[0])
        embeding = output.logits.detach().numpy()
        lb = np.argmax(embeding)
        res.append(lb)
    return res

def getlogit(txt):
    chunk_sample=split_chunk(txt)
    res = []
    for i in range(len(chunk_sample)):
        inp = tokenizer(chunk_sample[i], return_tensors='pt', padding="max_length", max_length=512)
        output = model(**inp)
        # output
        # output = F.softmax(output.pooler_output[0])
        embeding = output.logits
        lb = torch.max(torch.softmax(embeding[0], dim=0))
        res.append(lb.detach().numpy().tolist())
    return res

In [47]:
df['sentiment_label'] = df.nopunc.apply(getlb)
df

Unnamed: 0                                                txt        year  \
0           0  坚持罢工争取增资【新华社陕北十八日电】东京消息：日本海员工人继续大罢工。全日海员工会，在与政...  1948.12.20   
1           1  和平集会在纪念馆和平广场举行。侵华日军南京大屠杀遇难同胞纪念馆馆长朱成山表示，在这个具有纪念...  2012.08.16   

   text_length                                            txt_seg  Topic  \
0          470  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...    299   
1          686  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...    228   

   Doc_ID                                              Score  label  \
0   80956  [-0.17992433482732492, -0.1460053249588042, -0...      6   
1   38843  [0.015359698043600992, 0.03786564722019095, 0....      6   

             negative_score           positicve_score  positicve_score__mean  \
0   [0.7293623, 0.08481447]   [0.27063772, 0.9151855]               0.592912   
1  [0.49792624, 0.81404465]  [0.50207376, 0.18595535]               0.344015   

   negative_score_mean                                               text  \
0             0.407088  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...   
1             0.655985  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...   

                                              nopunc  \
0  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...   
1  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...   

                                              Phrase sentiment_label  
0  [坚持, 罢工, 争取, 增资, 新华社, 陕北, 十八日, 电, 东京, 消息, 日本海,...          [0, 1]  
1  [和平, 集会, 在, 纪念馆, 和平, 广场, 举行, 侵华日军南京大屠杀遇难同胞纪念馆,...          [1, 0]

In [48]:
df['pred_pro'] = df.nopunc.apply(getlogit)
df

Unnamed: 0                                                txt        year  \
0           0  坚持罢工争取增资【新华社陕北十八日电】东京消息：日本海员工人继续大罢工。全日海员工会，在与政...  1948.12.20   
1           1  和平集会在纪念馆和平广场举行。侵华日军南京大屠杀遇难同胞纪念馆馆长朱成山表示，在这个具有纪念...  2012.08.16   

   text_length                                            txt_seg  Topic  \
0          470  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...    299   
1          686  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...    228   

   Doc_ID                                              Score  label  \
0   80956  [-0.17992433482732492, -0.1460053249588042, -0...      6   
1   38843  [0.015359698043600992, 0.03786564722019095, 0....      6   

             negative_score           positicve_score  positicve_score__mean  \
0   [0.7293623, 0.08481447]   [0.27063772, 0.9151855]               0.592912   
1  [0.49792624, 0.81404465]  [0.50207376, 0.18595535]               0.344015   

   negative_score_mean                                               text  \
0             0.407088  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...   
1             0.655985  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...   

                                              nopunc  \
0  坚持 罢工 争取 增资 新华社 陕北 十八日 电 东京 消息 日本海 员工 人 继续 大 罢...   
1  和平 集会 在 纪念馆 和平 广场 举行 侵华日军南京大屠杀遇难同胞纪念馆 馆长 朱 成山 ...   

                                              Phrase sentiment_label  \
0  [坚持, 罢工, 争取, 增资, 新华社, 陕北, 十八日, 电, 东京, 消息, 日本海,...          [0, 1]   
1  [和平, 集会, 在, 纪念馆, 和平, 广场, 举行, 侵华日军南京大屠杀遇难同胞纪念馆,...          [1, 0]   

                                   pred_pro  
0  [0.7293623089790344, 0.9151855111122131]  
1  [0.5020737648010254, 0.8140446543693542]

### 可以先保存一个副本

In [ ]:
df.to_csv("/content/drive/MyDrive/第四轮验证集主动学习数据/al_0708_2.csv",index=False)
df.to_excel("/content/drive/MyDrive/第四轮验证集主动学习数据/al_0708_测试集.xlsx",index=False)

### 重新导入，在上面的操作跑过一次后，可以直接从这里开始（同一次数据流情况下）

In [ ]:
df = pd.read_csv("/content/drive/MyDrive/第四轮验证集主动学习数据/al_0708_2.csv")
df

Unnamed: 0                                             nopunc  \
0          627  中国 射击队 总教练 张福 我国 射击 健儿 将 在 第十届 亚运会 上 参加 十五个 项目...   
1        11337  新华社 二十八日 讯 人大常委会 副委员长 郭沫若 今天上午 接见 了 以 羽根 荣一 为首...   
2        23153  我队 以三比 击败 西德 队据 新华社 卢布尔雅那 十七日 电 第二十八届 世界 乒乓球 锦...   
3        10930  本报记者 张志文 俞懿春 陈然 为期 两天 的 海洋 争端 解决 国际法 研讨会 月 日 在...   
4        15512  自杀 已 成为 导致 日本 国家 公务员 死亡 的 第二 大 杀手 这是 日本 人事 院对 ...   
5         1891  据 新华社 北京 月 日电 国务院 副 总理 万里 今天上午 在 人民大会堂 会见 了 由 ...   
6        13232  北京 展出 董寿平 力作 九十九 幅 本报 北京 月 日 讯 记者 李德 润 罗雪村 报道 ...   
7        20575  七亿 中国 人民 必将 粉碎 一切 反华 挑衅 据 新华社 地拉那 十二日 电 阿尔巴尼亚 ...   
8        15576  阿曼苏丹国 位于 阿拉伯半岛 东南部 东北 濒 阿曼湾 东南 临 阿拉伯海 其 北端 隔 霍...   
9         4813  资产阶级 阴谋家 野心家 张春桥 以 马克思主义 理论家 自居 打着 马列主义 的 旗号 竭...   
10       16648  中日 五 团体 签署 共同声明 对 双方 签订 渔业 协定 表示 欢迎 新华社 九日 讯 中...   
11        4320  五年 内 将 跃居 世界 第一 据 新华社 日讯 我国 蚕丝 生产 将 在 第二个 五年计划...   
12        1711  英国 外事 报道 周刊 九月 十三日 的 一期 刊登 一篇 文章 标题 是 俄国 是 怎样 ...   
13         275  访 朝鲜 国家 观光 总局 副总 局长 黄正赏 本报 驻 朝鲜 记者 张 兴华 今天 旅游业...   
14       19289  苏修 胆敢 来犯 就 打断 它 的 脊梁骨 人民解放军 陆海空三 军 指战员 愤怒 声讨 苏...   
15       13117  胶东 沿海 人民 无限 愤慨 被 美机 扫射 的 十号 渔轮 全体 职工 们 表示 不能 忍...   
16        2617  记 西藏自治区 布达拉宫 消防大队 本报记者 徐锦庚 游客 来到 西藏 布达拉宫 是 必去 ...   
17        5175  纪念 苏军 建军 四十周年 郭沫若 在 我们 中国 远 在 三千年 前 的 殷商 就 标榜着...   
18       14625  据 新华社 日讯 东京 消息 正在 日本 访问 的 中国 农业 技术 代表团 结束 了 对 ...   
19       16428  李克强 欢迎 日本 经济界 三 团体 首次 联袂 访华 他 表示 中日 是 一衣带水 的 近...   
20       22839  社会主义 国家 人民 据 新华社 日讯 德意志民主共和国 捷克斯洛伐克 罗马尼亚 和 蒙古 ...   
21       10436  纪念 鲁迅 先生 诞生 九十 五周年 逝世 四十周年 鲁迅 在 日本 留学 期间 积极 参加...   
22       22475  吕叔湘 朱德熙 第三 讲 虚字 从前 人 没有 系统地 讲 语法 的 可是 知道 分别 实字...   
23       20371  本报 驻 美国 记者 吴乐珺 美国 贸易 代表 莱特 希泽月 日 宣布 正式 对 中国 发起...   
24       19892  药中 的 关木通 成分 含 马兜铃 酸 马兜铃 酸 导致 肾病 据 新华社 北京 月 日电 ...   
25        7961  许多 国家 使节 拒绝 出席 莫斯科 五一 观礼 活动 新华社 莫斯科 五月 一日 电 今年...   
26       20190  据 新华社 北京 月 日电 失传 千年 的 笋式 鸡 距笔 最近 在 安徽省 临泉县 的 临...   
27       12993  本报 特派记者 吴成良 自去 年月日 中国 东盟 自贸区 全面 启动 以来 双方 经贸关系 ...   
28        9774  新华社 东京 月 日电 记者 何德功 日本 宇宙 开发 事业团 近日 成功 研制 一种 机械...   
29       23984  据 新华社 华盛顿 月 日电 记者 符泉生 严锋 美以 巴 三方 首脑会晤 日 中午 在 美...   
30        4099  毛泽东思想 照亮 世界 人民 解放 的 道路 祝 世界 人民 伟大领袖 毛主席 万寿无疆 新...   
31       25497  各国 舆论 欢迎 老挝 三 亲王 达成协议 苏联 消息报 十二日 发表 评论员 的 文章 说...   
32       18080  纪念 抗日战争 胜利 四十周年 胡子昂 抗战 爆发 后 沿海 沿江 诸省 相继 沦陷 我们 ...   
33       17351  新华社 东京 五月 二十九日 电 华国锋 总理 今天下午 对 中国 在 日本 的 留学生 代...   
34        1853  在 党 的 十七届 五中全会 上 胡锦涛 总书记 明确指出 我国 仍 处于 可以 大有作为 ...   
35         313  中国 选手 夺得 七枚 金牌 第一届 亚洲 分龄 游泳 锦标赛 日 在 香港 开幕 中国 少...   
36        8792  本报讯 日本 著名 棋手 王立诚 九段 和 羽根 直树 九段 日前 正式 加盟 北京 海淀 ...   
37        2574  编辑 同志 我 是 一个 饱受 战争 和 黑暗 势力 迫害 回到 祖国 来 的 华侨 学生 ...   
38       10033  苏修 加紧 在 亚洲 拼凑 反华 包围圈 苏修 沿着 反华 反共 反革命 道路 走得 越远 ...   
39       22177  本报记者 刘阳 从 电视剧 人间正道 是 沧桑 老大 的 幸福 到 电影 十月 围城 金陵 ...   
40        2552  目前 海湾地区 战云密布 伊拉克 战争 一触即发 对于 这场 战争 的 胜负 人们 似乎 都...   
41        8562  党 的 十四大 以来 我国 外交 工作 述评 新华社 记者 本报记者 年代 特别 是 中国共...   
42       23273  日本 五千 和平 运动 积极分子 集会 强调 下届 禁止 氢弹 世界 大会 必须 是 团结 ...   
43       20636  侨联 副 主席 廖灿辉 发表谈话 本报讯 中华全国归国华侨联合会 副 主席 日本 归侨 廖灿...   
44       19145  本报 北京 月 日电 记者 王珂 商务部 外资 司 负责人 日 介绍 年 我国 实际 使用 ...   
45          68  各国 代表 支持 恢复 我 缔约国 地位 本报 乌拉圭 埃斯特角 月 日 专电 记者 管彦忠...   
46       23007  中方 呼吁 各方 为 会议 取得 积极 成果 共同努力 本报 北京 月 日 讯 记者 裴广江...   
47       13990  陈杰 何立强 中国 旅游 产业 节于 月 日 至 日 在 天津 举行 日前 我们 就 中国 ...   
48       16075  共祝 两国人民 新 的 一年 里 在 反对 美日 反动派 的 共同 斗争 中 取得 更大 胜...   
49        9349  本报记者 董洪亮 对 城乡 公办 小学 初中 实行 标准化 建设 这是 一个 重要 的 转折...   

                                                score  \
0   [0.03281145845671823, -0.017463615092265815, -...   
1   [0.29648743156719615, 0.32386012075554876, 0.1...   
2   [-0.08030344345551038, 0.21372191697900417, -0...   
3   [0.0788475778882582, 0.04253629233204423, -0.0...   
4   [0.6826887657522522, -0.019241865926012004, 0....   
5   [0.01826557824903283, 0.009975742460735359, 0....   
6   [-0.03636568767439275, 0.026390395554455118, -...   
7   [-0.06660478235447356, -

In [57]:
def cal_pro(df, i):
    #lb = literal_eval(df.iloc[i, -2])
    lb = df.iloc[i, -2]
    logits = df.iloc[i, -1]
    #logits = literal_eval(df.iloc[i, -1])
    num_1 = lb.count(1)
    num_0 = lb.count(0)
    cl = 0
    if num_1 >= num_0:
        cl = 1
    tmp_ind = [j for j,xj in enumerate(lb) if xj== cl]
    tem = np.zeros(len(tmp_ind))
#    print(tmp_ind)
#    print(logits[0])
    for k in range(len(tmp_ind)):
        tem[k] = logits[tmp_ind[k]]
    pred_pro = tem.mean()
    return (cl, pred_pro)

In [59]:
for i in range(0,2):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,7]))#2
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(ts))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            df.iloc[i,-3],
    #                         delta
                            0.0)
    print([position_vis1])
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
0 -th
torch.Size([233])
233
<class 'torch.Tensor'>
<class 'list'>
 Visualizations For Position 


--------------------------------------------------------------------------------
1 -th
torch.Size([319])
300
<class 'torch.Tensor'>
<class 'list'>
 Visualizations For Position 


In [ ]:
for i in range(1,3):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
1 -th
torch.Size([33])
205
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
2 -th
torch.Size([384])
2333
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(3,5):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
3 -th
torch.Size([1038])
6164
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
4 -th
torch.Size([74])
443
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(5,7):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
5 -th
torch.Size([183])
1103
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
6 -th
torch.Size([165])
1018
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(7,9):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
7 -th
torch.Size([330])
1953
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
8 -th
torch.Size([278])
1670
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(9,10):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
9 -th
torch.Size([324])
1967
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(10,12):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
10 -th
torch.Size([358])
2128
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
11 -th
torch.Size([486])
2831
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(12,15):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
12 -th
torch.Size([1078])
6364
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
13 -th
torch.Size([526])
3107
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
14 -th
torch.Size([211])
1286
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(15,18):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
15 -th
torch.Size([320])
1904
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
16 -th
torch.Size([884])
5299
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
17 -th
torch.Size([339])
2004
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(18,20):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
18 -th
torch.Size([88])
528
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
19 -th
torch.Size([331])
2004
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(20,23):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
20 -th
torch.Size([1512])
9073
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
21 -th
torch.Size([420])
2524
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
22 -th
torch.Size([2195])
12424
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(23,25):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
23 -th
torch.Size([888])
5260
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
24 -th
torch.Size([189])
1112
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(25,28):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
25 -th
torch.Size([77])
473
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
26 -th
torch.Size([105])
609
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
27 -th
torch.Size([896])
5367
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(28,30):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
28 -th
torch.Size([120])
707
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
29 -th
torch.Size([220])
1332
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(30,33):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
30 -th
torch.Size([1419])
8543
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
31 -th
torch.Size([626])
3701
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
32 -th
torch.Size([763])
4518
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(33,35):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
33 -th
torch.Size([142])
845
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
34 -th
torch.Size([1274])
7548
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(35,38):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
35 -th
torch.Size([136])
798
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
36 -th
torch.Size([129])
765
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
37 -th
torch.Size([307])
1766
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(38,40):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
38 -th
torch.Size([968])
5823
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
39 -th
torch.Size([785])
4648
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(40,43):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
40 -th
torch.Size([872])
5163
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
41 -th
torch.Size([1983])
11833
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
42 -th
torch.Size([192])
1138
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(43,45):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
43 -th
torch.Size([70])
440
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
44 -th
torch.Size([220])
1327
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(45,48):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
45 -th
torch.Size([146])
889
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
46 -th
torch.Size([436])
2634
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
47 -th
torch.Size([744])
4471
<class 'str'>
 Visualizations For Position 


In [ ]:
for i in range(48,50):
    print("--------"*10)
    print(i,"-th")
    ts = torch.Tensor(literal_eval(df.iloc[i,2]))
    print(ts.shape)
    print(len(df.iloc[i,-3]))
    print(type(df.iloc[i,-3]))
    cl, pred_pro = cal_pro(df, i)
    # storing couple samples in an array for visualization purposes
    position_vis1 = viz.VisualizationDataRecord(
                            ts,
                            pred_pro,
                            cl,
                            cl,
                            cl,
                            ts.sum(),       
                            literal_eval(df.iloc[i,-3]),
    #                         delta
                            0.0)
    print('\033[1m', 'Visualizations For Position', '\033[0m')
    viz.visualize_text([position_vis1])

--------------------------------------------------------------------------------
48 -th
torch.Size([329])
1970
<class 'str'>
 Visualizations For Position 


--------------------------------------------------------------------------------
49 -th
torch.Size([835])
4960
<class 'str'>
 Visualizations For Position 
